In [13]:
import os
import sys

sys.path.append(os.path.join(os.path.sep, *os.getcwd().split(os.path.sep)[:-2]))

In [14]:
import numpy as np
import pandas as pd

In [15]:
import pulp

In [16]:
import time

In [17]:
from src.modeling import *

In [18]:
def of_net_income(_cost, _vars, _crops_year):
    return pulp.lpSum([getattr(_cost, _crops_year[i]) * _vars[i] for i in _crops_year])

def of_ua_total(_vars, _crops_year):
    return pulp.lpSum([_vars[i] for i in _crops_year])

def of_crop_diversity(_vars, _crops_year):
    return pulp.lpSum([_vars[i] for i in _crops_year])

In [19]:
sig = lambda sigma, NUM_ITER: 1/(1 + np.exp(sigma*(np.linspace(0, NUM_ITER, NUM_ITER)-(NUM_ITER/2))))

alpha_lin = np.linspace(0, 1, 1000)
alpha_sig_004 = sig(-0.004, 1000)
alpha_sig_06 = sig(-0.06, 1000)

l_alpha = {'alpha_lin':     alpha_lin, 
           'alpha_sig_004': alpha_sig_004, 
           'alpha_sig_06':  alpha_sig_06,
           }

In [20]:
DATA_PATH = '../../data/al_rasheed'
RESULTS_PATH = '../../results/data/al_rasheed/model_1/wsum'

In [21]:
variables = pd.read_csv(f'{DATA_PATH}/variables.csv', sep=';')
income = pd.read_csv(f'{DATA_PATH}/net_income.csv', sep=';')
constraints = pd.read_csv(f'{DATA_PATH}/constraints.csv', sep=';')
rotations = pd.read_csv(f'{DATA_PATH}/rotations.csv', sep=';').fillna(0)

In [22]:
#YEARS = 2

In [23]:
crops = variables.variable.to_list()

crops_year_integer = dict(zip([f"y{i:03}_int_{j}" for i in range(1,YEARS+1) for j in crops], YEARS*crops))

crops_year_binary = dict(zip([f"y{i:03}_bin_{j}" for i in range(1,YEARS+1) for j in crops], YEARS*crops))

In [24]:
variables.set_index(keys='variable', inplace=True)

integer_vars = create_integer_vars(crops_year_integer, variables)

binary_vars = create_binary_vars(crops_year_binary, variables)

In [25]:
ofs = [of_net_income(income.loc[0,:], integer_vars, crops_year_integer),
       of_ua_total(integer_vars, crops_year_integer),
       of_crop_diversity(binary_vars, crops_year_binary)]

In [26]:
min_max_ofs = []
for of in ofs:
    vl = []
    for opt in [pulp.LpMinimize, pulp.LpMaximize]:
        model = pulp.LpProblem("Modelo_1", opt)
        model += of
        const_idx = add_constraints(model, integer_vars, constraints, crops_year_integer, len(crops), YEARS, const_id = 0)
        const_idx = add_binary_correlation(model, binary_vars, integer_vars, 113, const_id = const_idx)
        const_idx = add_crop_rotation_constraints(model, integer_vars, crops_year_integer, rotations, YEARS, crops, 'y{:03d}_int_{}', const_idx)

        solution = model.solve(pulp.GLPK())

        vl.append(pulp.value(model.objective))
    
    min_max_ofs.append(vl)

GLPSOL--GLPK LP/MIP Solver 5.0
Parameter(s) specified in the command line:
 --cpxlp /tmp/5481d9ed4d164f3ea8f8c84cf1c28e61-pulp.lp -o /tmp/5481d9ed4d164f3ea8f8c84cf1c28e61-pulp.sol
Reading problem data from '/tmp/5481d9ed4d164f3ea8f8c84cf1c28e61-pulp.lp'...
88 rows, 48 columns, 430 non-zeros
48 integer variables, 24 of which are binary
311 lines were read
GLPK Integer Optimizer 5.0
88 rows, 48 columns, 430 non-zeros
48 integer variables, 24 of which are binary
Preprocessing...
24 constraint coefficient(s) were reduced
64 rows, 48 columns, 242 non-zeros
48 integer variables, 24 of which are binary
Scaling...
 A: min|aij| =  1.000e+00  max|aij| =  2.260e+03  ratio =  2.260e+03
GM: min|aij| =  4.453e-01  max|aij| =  2.246e+00  ratio =  5.042e+00
EQ: min|aij| =  2.100e-01  max|aij| =  1.000e+00  ratio =  4.761e+00
2N: min|aij| =  1.104e-01  max|aij| =  1.562e+00  ratio =  1.416e+01
Constructing initial basis...
Size of triangular part is 64
Solving LP relaxation...
GLPK Simplex Optimizer 5.

In [27]:
ofs_norn = [ min_max_normalization(ofs[idx], min_max_ofs[idx]) for idx in range(len(ofs))]

In [28]:
solution_lst = []
for key in l_alpha:
    aph = l_alpha[key]
    for i_alpha in range(0, len(aph)):            
        alpha = aph[i_alpha]

        start_time = time.time()
        model = pulp.LpProblem("First_Model", pulp.LpMaximize)

        weighted_sum(model, ofs_norn, [alpha, 0.5 * (1 - alpha), 0.5 * (1 - alpha)]) 

        const_idx = add_constraints(model, integer_vars, constraints, crops_year_integer, len(crops), YEARS, const_id = 0)
        const_idx = add_binary_correlation(model, binary_vars, integer_vars, 113, const_id = const_idx)
        const_idx = add_crop_rotation_constraints(model, integer_vars, crops_year_integer, rotations, YEARS, crops, 'y{:03d}_int_{}', const_idx)

        solution = model.solve(pulp.GLPK())

        end_time = time.time()

        integer_var_values = {key: pulp.value(value) for key, value in integer_vars.items()}
        binary_var_values = {key: pulp.value(value) for key, value in binary_vars.items()}

        ney_incone_ofs_values = sum_cost_of_values(income.loc[0,:], integer_var_values, crops_year_integer, 'net_income', 0, 4)
        us_ofs_values = sum_of_var_values(integer_var_values, 'ua', 0, 4)
        crop_diversity_ofs_values = sum_of_var_values(binary_var_values, 'crop_diversity', 0, 4)


        solution_lst.append([key,
                            end_time - start_time,
                            i_alpha,
                            alpha,
                            str(pulp.LpStatus[solution])] +
                            list(integer_var_values.values())+
                            list(binary_var_values.values())+
                            [pulp.value(model.objective)] +
                            list(ney_incone_ofs_values.values())+
                            list(us_ofs_values.values())+
                            list(crop_diversity_ofs_values.values())
                            )


GLPSOL--GLPK LP/MIP Solver 5.0
Parameter(s) specified in the command line:
 --cpxlp /tmp/e0e20c80bb9c43e88ed4c491110b415f-pulp.lp -o /tmp/e0e20c80bb9c43e88ed4c491110b415f-pulp.sol
Reading problem data from '/tmp/e0e20c80bb9c43e88ed4c491110b415f-pulp.lp'...
88 rows, 48 columns, 430 non-zeros
48 integer variables, 24 of which are binary
326 lines were read
GLPK Integer Optimizer 5.0
88 rows, 48 columns, 430 non-zeros
48 integer variables, 24 of which are binary
Preprocessing...
24 constraint coefficient(s) were reduced
64 rows, 48 columns, 242 non-zeros
48 integer variables, 24 of which are binary
Scaling...
 A: min|aij| =  1.000e+00  max|aij| =  2.260e+03  ratio =  2.260e+03
GM: min|aij| =  4.453e-01  max|aij| =  2.246e+00  ratio =  5.042e+00
EQ: min|aij| =  2.100e-01  max|aij| =  1.000e+00  ratio =  4.761e+00
2N: min|aij| =  1.104e-01  max|aij| =  1.562e+00  ratio =  1.416e+01
Constructing initial basis...
Size of triangular part is 64
Solving LP relaxation...
GLPK Simplex Optimizer 5.

In [29]:
columns = ["alpha_type", "time", "iter", "alpha", "status"] +\
         list(integer_var_values.keys()) + \
         list(binary_var_values.keys()) + \
         ['OF_Optimized'] + \
         list(ney_incone_ofs_values.keys()) + \
         list(us_ofs_values.keys()) + \
         list(crop_diversity_ofs_values.keys())

In [30]:
results = pd.DataFrame(solution_lst, columns=columns)

In [31]:
results.to_csv(f'{RESULTS_PATH}/WeightedSum_y{YEARS:03}.csv', sep=';', index=False)